# For an analysis competition...
What to predict?
- age ... too few nans (prediction may be meaningless...)
- cancellation of premium membership

# Libraries

In [1]:
# basics
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import gc
import json
import time
import datetime
import os
import sys
import pickle
from sklearn.model_selection import train_test_split, StratifiedKFold

# visualize
import matplotlib.pyplot as plt
import matplotlib.style as style
from matplotlib_venn import venn2
import seaborn as sns
from matplotlib import pyplot
from matplotlib.ticker import ScalarFormatter
import plotly.figure_factory as ff
import plotly.express as px
import missingno as msno

sns.set_context("talk")
# sns.set_style("ticks", {"xtick.major.size": 8, "ytick.major.size": 8})
style.use('fivethirtyeight')

# custom EDA functions
mypath = os.getcwd()
sys.path.append(mypath + '/code/') 
from utils import reduce_mem_usage
from categorical_encoder import label_encoding
from catplot import CategoricalVisualizer
from denseplot import DenseVisualizer

# custom modeling functions
sys.path.append(mypath + '/cls_models/') 
from base_classifier import ClassifierBase
from lgb_classifier import LgbClassifier
from catb_classifier import CatbClassifier

# stats
from scipy import stats
from sklearn.metrics import cohen_kappa_score, mean_squared_error, mean_absolute_error
from sklearn.model_selection import KFold, StratifiedKFold, GroupKFold
from sklearn.model_selection import train_test_split
import scipy as sp
from functools import partial
from collections import Counter

pd.set_option('display.max_rows', None)

import warnings
warnings.filterwarnings('ignore')

print("libraries imported")

libraries imported


/opt/anaconda3/lib/python3.7/site-packages/lightgbm/__init__.py:48: UserWarning:

Starting from version 2.2.1, the library file in distribution wheels for macOS is built by the Apple Clang (Xcode_8.3.3) compiler.
This means that in case of installing LightGBM from PyPI via the ``pip install lightgbm`` command, you don't need to install the gcc compiler anymore.
Instead of that, you need to install the OpenMP library, which is required for running LightGBM on the system with the Apple Clang compiler.
You can install the OpenMP library by the following command: ``brew install libomp``.



# Load data

In [2]:
!ls

EDA.ipynb            cls_models           reg_models
EDA_houseprice.ipynb code
EDA_laputa.ipynb     inputs


In [3]:
# check path
datapath = "inputs/"
datapath = "/Volumes/sec/anemos-poc-large-sec/users/kakawagu/data/laputa_comp"
files = os.listdir(datapath)
print(files)

['laputa.csv']


In [4]:
# import data
time0 = time.time()

train = pd.read_csv(datapath + '/laputa.csv', index_col=0)
# test = pd.read_csv(datapath + '/test.csv')
# submission = pd.read_csv(datapath + '/sample_submission.csv')

time1 = time.time()
print(time1 - time0, " seconds to load data")

44.2320499420166  seconds to load data


In [5]:
# check train
print(train.shape)
train.head()

(10000, 1021)


y_id_hex  1_y_id_master_gender  1_y_id_master_birthday  \
0  000081BEB28F85B6DE                     2                     NaN   
1  0000DC88EA731D5BFC                     1                     NaN   
2  0000D9F6A83EA4C67C                     2                     NaN   
3  00088B68DFA836DEBE                     1                     NaN   
4  0007596AE753E853D9                     1                     NaN   

   1_y_id_master_registration_date  1_y_id_master_first_update  \
0                         20140518                  20140525.0   
1                         20030216                  20080701.0   
2                         20160424                  20160426.0   
3                         20150111                  20150116.0   
4                         20190901                  20190905.0   

   1_y_id_master_last_update  1_y_id_master_age  \
0                   20191201               37.0   
1                   20191201               38.0   
2                   20191130               38.0   
3                   20191119               28.0   
4                   20191104               23.0   

   1_y_id_master_registration_month  1_y_id_master_registration_week  \
0                                67                              289   
1                               202                              876   
2                                44                              188   
3                                59                              255   
4                                 3                               13   

   1_y_id_master_chkyj_flag  ...  \
0                     False  ...   
1                     False  ...   
2                     False  ...   
3                     False  ...   
4                     False  ...   

   99_yup_user_daily_score_2_interest_know_well_world_history  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   99_yup_user_daily_score_2_interest_know_well_art  \
0                                               NaN   
1                                               NaN   
2                                               NaN   
3                                               NaN   
4                                               NaN   

   99_yup_user_daily_score_2_interest_know_well_iphone  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

  99_yup_user_daily_score_2_interest_know_well_android  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

  99_yup_user_daily_score_2_interest_know_well_pc  \
0                                             NaN   
1                                        0.022498   
2                                             NaN   
3                                             NaN   
4                                             NaN   

  99_yup_user_daily_score_2_interest_know_well_home_appliance  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   99_yup_user_daily_score_2_interest_starting_own_business  \
0                                      

# EDA

In [6]:
train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10000 entries, 0 to 9999
Columns: 1021 entries, y_id_hex to 99_yup_user_daily_score_2_interest_know_well_construction
dtypes: bool(6), float64(911), int64(17), object(87)
memory usage: 77.6+ MB


In [7]:
train.dtypes

y_id_hex                                                                           object
1_y_id_master_gender                                                                int64
1_y_id_master_birthday                                                            float64
1_y_id_master_registration_date                                                     int64
1_y_id_master_first_update                                                        float64
1_y_id_master_last_update                                                           int64
1_y_id_master_age                                                                 float64
1_y_id_master_registration_month                                                    int64
1_y_id_master_registration_week                                                     int64
1_y_id_master_chkyj_flag                                                             bool
2_user_profile_master_commerce_registration_month                                   int64
2_user_pro

In [8]:
# missing data?
import missingno as msno
msno.matrix(df=train, figsize=(20,14), color=(0.5,0,0))

In [9]:
premium_features = []
for f in train.columns.values.tolist():
    if "premium_user_master" in f:
        premium_features.append(f)
        print(f)

10_premium_user_master_last_order_date
10_premium_user_master_premium_segment_id
10_premium_user_master_service_code
10_premium_user_master_channel_id
10_premium_user_master_campaign_id
10_premium_user_master_discount_id
10_premium_user_master_cancel_flag
10_premium_user_master_cancel_date
10_premium_user_master_cancel_type
10_premium_user_master_registration_day
10_premium_user_master_registration_month
10_premium_user_master_sbm_type
10_premium_user_master_first_order_date
10_premium_user_master_order_count


In [10]:
train[premium_features].head()

10_premium_user_master_last_order_date  \
0                                     NaN   
1                              20190326.0   
2                                     NaN   
3                              20170601.0   
4                                     NaN   

   10_premium_user_master_premium_segment_id  \
0                                        NaN   
1                                        2.0   
2                                        NaN   
3                                        1.0   
4                                        NaN   

   10_premium_user_master_service_code 10_premium_user_master_channel_id  \
0                                  NaN                               NaN   
1                               2432.0                          C0ymb001   
2                                  NaN                               NaN   
3                               2419.0                               NaN   
4                                  NaN                               NaN   

  10_premium_user_master_campaign_id  10_premium_user_master_discount_id  \
0                                NaN                                 NaN   
1                           A-140601                         800000924.0   
2                                NaN                                 NaN   
3                                NaN                         800001066.0   
4                                NaN                                 NaN   

  10_premium_user_master_cancel_flag  10_premium_user_master_cancel_date  \
0                                NaN                                 NaN   
1                              False                                 NaN   
2                                NaN                                 NaN   
3                               True                          20180420.0   
4                                NaN                                 NaN   

   10_premium_user_master_cancel_type  \
0                                 NaN   
1                                 NaN   
2                                 NaN   
3                                 2.0   
4                                 NaN   

   10_premium_user_master_registration_day  \
0                                      NaN   
1                                    297.0   
2                                      NaN   
3                                      0.0   
4                                      NaN   

   10_premium_user_master_registration_month  10_premium_user_master_sbm_type  \
0                                        NaN                              NaN   
1                                        9.0                              0.0   
2                                        NaN                              NaN   
3                                        0.0                              5.0   
4                                        NaN                              NaN   

   10_premium_user_master_first_order_date  10_premium_user_master_order_count  
0                                      NaN                                 NaN  
1                               20030707.0                                 6.0  
2                                      NaN                                 NaN  
3                               20170601.0                                 1.0  
4                                      NaN                                 NaN

In [11]:
train["10_premium_user_master_cancel_flag"].dtype

dtype('O')

In [12]:
train["1_y_id_master_age"].isna().sum() / train.shape[0]

0.0218

# Target

In [13]:
# remove nan from target
target = "10_premium_user_master_cancel_flag"
train = train.loc[train[target].isna().values == False, :].reset_index(drop=True, inplace=False)

train[target].value_counts()

False    3018
True     1209
Name: 10_premium_user_master_cancel_flag, dtype: int64

In [14]:
train[target] = train[target].astype(int)
train[target].value_counts()

0    3018
1    1209
Name: 10_premium_user_master_cancel_flag, dtype: int64

In [15]:
# hist
fig, ax = plt.subplots(1, 1, figsize=(6, 4))
sns.countplot(x=target, data=train, ax=ax)
ax.xaxis.set_major_formatter(ScalarFormatter(useMathText=True))
ax.ticklabel_format(style="sci",  axis="x",scilimits=(0,0))
ax.yaxis.set_major_formatter(ScalarFormatter(useMathText=True))
ax.ticklabel_format(style="sci",  axis="y",scilimits=(0,0))
ax.set_title("nnans = {}, {}%".format(train[target].isna().sum(), 100 * train[target].isna().sum() / train.shape[0]))
ax.set_xlabel(target)
ax.set_ylabel("#")

Text(0, 0.5, '#')

In [16]:
# roughly categorize features
cat_features = []
dense_features = []
for f in train.columns.values.tolist():
    if f != target:
        if (train[f].dtype == "object") | (train[f].dtype == "bool"):
            cat_features.append(f)
        else:
            dense_features.append(f)
features = dense_features + cat_features
print(f"There are {len(features)} features.")
print(f"There are {len(dense_features)} dense features.")
print(f"There are {len(cat_features)} categorical features.")

There are 1020 features.
There are 928 dense features.
There are 92 categorical features.


# Train, test split

In [17]:
kf = StratifiedKFold(n_splits=5, random_state=1220, shuffle=True)
for fold, (train_index, test_index) in enumerate(kf.split(train, train[target].values)):
    if fold == 0:
        X_train, X_test = train.loc[train_index, :], train.loc[test_index, :]
        y_train, y_test = train.loc[train_index, target], train.loc[test_index, target]
    else:
        pass

In [18]:
print(X_train.shape)
X_train.head()

(3381, 1021)


y_id_hex  1_y_id_master_gender  1_y_id_master_birthday  \
0  0000DC88EA731D5BFC                     1                     NaN   
1  00088B68DFA836DEBE                     1                     NaN   
2  0003C8DA499B07FE8C                     1                     NaN   
3  00077071089DC5AA3D                     1                     NaN   
4  0000CFBA992DE7AB41                     2                     NaN   

   1_y_id_master_registration_date  1_y_id_master_first_update  \
0                         20030216                  20080701.0   
1                         20150111                  20150116.0   
2                         20170212                  20170217.0   
3                         20080810                  20080814.0   
4                         20170611                  20170617.0   

   1_y_id_master_last_update  1_y_id_master_age  \
0                   20191201               38.0   
1                   20191119               28.0   
2                   20191130               53.0   
3                   20191201               39.0   
4                   20191201               46.0   

   1_y_id_master_registration_month  1_y_id_master_registration_week  \
0                               202                              876   
1                                59                              255   
2                                34                              146   
3                               136                              590   
4                                30                              129   

   1_y_id_master_chkyj_flag  ...  \
0                     False  ...   
1                     False  ...   
2                     False  ...   
3                     False  ...   
4                     False  ...   

   99_yup_user_daily_score_2_interest_know_well_world_history  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   99_yup_user_daily_score_2_interest_know_well_art  \
0                                               NaN   
1                                               NaN   
2                                               NaN   
3                                               NaN   
4                                          0.035332   

   99_yup_user_daily_score_2_interest_know_well_iphone  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

  99_yup_user_daily_score_2_interest_know_well_android  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

  99_yup_user_daily_score_2_interest_know_well_pc  \
0                                        0.022498   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

  99_yup_user_daily_score_2_interest_know_well_home_appliance  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                           0.026999            
4                                           0.006862            

   99_yup_user_daily_score_2_interest_starting_own_business  \
0                                      

In [19]:
print(X_test.shape)
X_test.head()

(846, 1021)


y_id_hex  1_y_id_master_gender  1_y_id_master_birthday  \
6   00091D0CB89425297A                     2                     NaN   
9   00088DC755AA1FFBF5                     1                     NaN   
18  0004F7E6A17F349216                     1                     NaN   
28  0006BD9ADDEA3169CB                     1                     NaN   
30  0007DBDDC929063B09                     2                     NaN   

    1_y_id_master_registration_date  1_y_id_master_first_update  \
6                          20170430                  20170503.0   
9                          20030420                  20080630.0   
18                         20170521                  20170526.0   
28                         20080127                  20080629.0   
30                         20150503                  20150504.0   

    1_y_id_master_last_update  1_y_id_master_age  \
6                    20191106               72.0   
9                    20191201               46.0   
18                   20191117               37.0   
28                   20191201               46.0   
30                   20191201               19.0   

    1_y_id_master_registration_month  1_y_id_master_registration_week  \
6                                 32                              135   
9                                200                              867   
18                                31                              132   
28                               143                              618   
30                                55                              239   

    1_y_id_master_chkyj_flag  ...  \
6                      False  ...   
9                      False  ...   
18                     False  ...   
28                     False  ...   
30                     False  ...   

    99_yup_user_daily_score_2_interest_know_well_world_history  \
6                                                 NaN            
9                                                 NaN            
18                                                NaN            
28                                                NaN            
30                                                NaN            

    99_yup_user_daily_score_2_interest_know_well_art  \
6                                                NaN   
9                                           0.062455   
18                                               NaN   
28                                               NaN   
30                                               NaN   

    99_yup_user_daily_score_2_interest_know_well_iphone  \
6                                                 NaN     
9                                            0.028861     
18                                                NaN     
28                                           0.046852     
30                                                NaN     

   99_yup_user_daily_score_2_interest_know_well_android  \
6                                                 NaN     
9                                            0.198244     
18                                                NaN     
28                                           0.059086     
30                                                NaN     

   99_yup_user_daily_score_2_interest_know_well_pc  \
6                                              NaN   
9                                         0.070231   
18                                             NaN   
28                                        0.079213   
30                                             NaN   

   99_yup_user_daily_score_2_interest_know_well_home_appliance  \
6                                                 NaN            
9                                            0.076969            
18                                                NaN            
28                                                NaN            
30                                                NaN            

    99_yup_user_daily_score_2_interes

# Dense features

In [20]:
vd = DenseVisualizer(train=X_train, test=X_test, features=dense_features, target=target)
chkd = vd.column_checker()
print(chkd.shape)
chkd.head()

feature name = 1_y_id_master_gender
feature name = 1_y_id_master_birthday
feature name = 1_y_id_master_registration_date
feature name = 1_y_id_master_first_update
feature name = 1_y_id_master_last_update
feature name = 1_y_id_master_age
feature name = 1_y_id_master_registration_month
feature name = 1_y_id_master_registration_week
feature name = 2_user_profile_master_commerce_registration_month
feature name = 2_user_profile_master_commerce_gender
feature name = 2_user_profile_master_commerce_age
feature name = 2_user_profile_master_commerce_tcard_status
feature name = 2_user_profile_master_commerce_preimum_registration_month
feature name = 2_user_profile_master_commerce_premium_segment_id
feature name = 2_user_profile_master_commerce_wallet_registration_month
feature name = 2_user_profile_master_commerce_shopping_order_count
feature name = 2_user_profile_master_commerce_shopping_avg_total_price
feature name = 2_user_profile_master_commerce_shopping_avg_order_day
feature name = 2_user_pr

feature name = 8_app_user_monthly_stats_sportsnavi_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_ymobile_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_ysmartsecurity_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_yjcal_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_yfiler_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_apps_map_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_apps_navi_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_finance_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_ybackup_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_chiebukuro_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_yqrcode_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_launcher_buzzhome_first_activate_date_monthly
feature name = 8_app_user_monthly_stats_ebookjapan_first_activate

feature name = 8_app_user_monthly_stats_gyao_activate_day
feature name = 8_app_user_monthly_stats_auctions_activate_day
feature name = 8_app_user_monthly_stats_mail_activate_day
feature name = 8_app_user_monthly_stats_yjtrend_activate_day
feature name = 8_app_user_monthly_stats_apppkgcal_activate_day
feature name = 8_app_user_monthly_stats_ymail_activate_day
feature name = 8_app_user_monthly_stats_emg_activate_day
feature name = 8_app_user_monthly_stats_ysmarttool_activate_day
feature name = 8_app_user_monthly_stats_ybrowser_activate_day
feature name = 8_app_user_monthly_stats_ynaviapp_activate_day
feature name = 8_app_user_monthly_stats_npb_textlive_activate_day
feature name = 8_app_user_monthly_stats_maps_activate_day
feature name = 8_app_user_monthly_stats_sportsnavi_activate_day
feature name = 8_app_user_monthly_stats_ymobile_activate_day
feature name = 8_app_user_monthly_stats_ysmartsecurity_activate_day
feature name = 8_app_user_monthly_stats_yjcal_activate_day
feature name = 8_a

feature name = 8_app_user_monthly_stats_mail_duration
feature name = 8_app_user_monthly_stats_yjtrend_duration
feature name = 8_app_user_monthly_stats_apppkgcal_duration
feature name = 8_app_user_monthly_stats_ymail_duration
feature name = 8_app_user_monthly_stats_emg_duration
feature name = 8_app_user_monthly_stats_ysmarttool_duration
feature name = 8_app_user_monthly_stats_ybrowser_duration
feature name = 8_app_user_monthly_stats_ynaviapp_duration
feature name = 8_app_user_monthly_stats_npb_textlive_duration
feature name = 8_app_user_monthly_stats_maps_duration
feature name = 8_app_user_monthly_stats_sportsnavi_duration
feature name = 8_app_user_monthly_stats_ymobile_duration
feature name = 8_app_user_monthly_stats_ysmartsecurity_duration
feature name = 8_app_user_monthly_stats_yjcal_duration
feature name = 8_app_user_monthly_stats_yfiler_duration
feature name = 8_app_user_monthly_stats_apps_map_duration
feature name = 8_app_user_monthly_stats_apps_navi_duration
feature name = 8_app_

feature name = 8_app_user_monthly_stats_ysmartsecurity_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_yjcal_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_yfiler_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_apps_map_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_apps_navi_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_finance_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_ybackup_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_chiebukuro_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_yqrcode_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_launcher_buzzhome_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_ebookjapan_last_widget_activate_date_monthly
feature name = 8_app_user_monthly_stats_pmall_last_widget_activate_date_mon

feature name = 25_ycard_apply_info_business_code
feature name = 25_ycard_apply_info_driver_license_type
feature name = 25_ycard_apply_info_household_num
feature name = 25_ycard_apply_info_purpose_type
feature name = 25_ycard_apply_info_rank1
feature name = 25_ycard_apply_info_rank6
feature name = 25_ycard_apply_info_rank7
feature name = 25_ycard_apply_info_rank8
feature name = 25_ycard_apply_info_rank9
feature name = 99_yup_user_daily_score_attribute_residence_urban
feature name = 99_yup_user_daily_score_attribute_homemaker
feature name = 99_yup_user_daily_score_attribute_engineer
feature name = 99_yup_user_daily_score_attribute_family_baby
feature name = 99_yup_user_daily_score_attribute_family_infant
feature name = 99_yup_user_daily_score_attribute_property_glasses
feature name = 99_yup_user_daily_score_attribute_property_bicycle
feature name = 99_yup_user_daily_score_attribute_property_car
feature name = 99_yup_user_daily_score_attribute_smoking
feature name = 99_yup_user_daily_scor

feature name = 99_yup_user_daily_score_interest_mlb
feature name = 99_yup_user_daily_score_interest_highschool_baseball
feature name = 99_yup_user_daily_score_interest_j_league
feature name = 99_yup_user_daily_score_interest_world_football
feature name = 99_yup_user_daily_score_interest_horse_racing
feature name = 99_yup_user_daily_score_2_interest_golf
feature name = 99_yup_user_daily_score_2_interest_figure_skating
feature name = 99_yup_user_daily_score_2_interest_f1
feature name = 99_yup_user_daily_score_2_interest_tennis
feature name = 99_yup_user_daily_score_2_interest_basketball
feature name = 99_yup_user_daily_score_2_interest_martial_arts
feature name = 99_yup_user_daily_score_2_interest_sumo
feature name = 99_yup_user_daily_score_2_interest_mens_fashion
feature name = 99_yup_user_daily_score_2_interest_ladies_fashion
feature name = 99_yup_user_daily_score_2_interest_mens_shoes
feature name = 99_yup_user_daily_score_2_interest_comic
feature name = 99_yup_user_daily_score_2_inte

features  train_nans  test_nans  train_nunique  \
0             1_y_id_master_gender           0          0              3   
1           1_y_id_master_birthday        3381        846              0   
2  1_y_id_master_registration_date           0          0            972   
3       1_y_id_master_first_update         133         29           1624   
4        1_y_id_master_last_update           0          0             31   

   test_nunique   train_min    test_min   train_max    test_max    train_mean  \
0             3         0.0         0.0         2.0         2.0  1.403135e+00   
1             0         NaN         NaN         NaN         NaN           NaN   
2           547  19980726.0  19980726.0  20191124.0  20191124.0  2.011548e+07   
3           534  20080629.0  20080629.0  20191201.0  20191130.0  2.013169e+07   
4            29  20191101.0  20191101.0  20191201.0  20191201.0  2.019118e+07   

      test_mean  train_skew  test_skew  
0  1.405437e+00    0.098926   0.079403  
1           NaN         NaN        NaN  
2  2.011488e+07   -0.402527  -0.410383  
3  2.013101e+07   -0.054323  -0.056354  
4  2.019118e+07   -1.348543  -1.334516

In [21]:
chkd.style.background_gradient()

In [22]:
# remove features with too many nans
dense_features = chkd.loc[chkd["train_nans"] < 3000, "features"].values.tolist()
print(dense_features)

['1_y_id_master_gender', '1_y_id_master_registration_date', '1_y_id_master_first_update', '1_y_id_master_last_update', '1_y_id_master_age', '1_y_id_master_registration_month', '1_y_id_master_registration_week', '2_user_profile_master_commerce_registration_month', '2_user_profile_master_commerce_gender', '2_user_profile_master_commerce_age', '2_user_profile_master_commerce_tcard_status', '2_user_profile_master_commerce_preimum_registration_month', '2_user_profile_master_commerce_premium_segment_id', '2_user_profile_master_commerce_wallet_registration_month', '2_user_profile_master_commerce_shopping_order_count', '2_user_profile_master_commerce_shopping_avg_total_price', '2_user_profile_master_commerce_shopping_avg_order_day', '2_user_profile_master_commerce_shopping_last_order_day', '2_user_profile_master_commerce_auction_won_count', '2_user_profile_master_commerce_auction_avg_won_price', '2_user_profile_master_commerce_auction_avg_won_day', '2_user_profile_master_commerce_auction_last_

# Categorical features

In [23]:
# EDA for categorical features
vc = CategoricalVisualizer(train=X_train, test=X_test, features=cat_features, target=target)
chkc = vc.column_checker()
print(chkc.shape)
chkc.head()

feature name = y_id_hex
feature name = 1_y_id_master_chkyj_flag
feature name = 2_user_profile_master_commerce_generation1
feature name = 2_user_profile_master_commerce_generation3
feature name = 2_user_profile_master_commerce_generation5
feature name = 2_user_profile_master_commerce_chkyj_flag
feature name = 2_user_profile_master_commerce_premium_user_flag
feature name = 2_user_profile_master_commerce_wallet_registered_flag
feature name = 2_user_profile_master_commerce_valid_card_count
feature name = 2_user_profile_master_commerce_auction_store_flag
feature name = 6_point_user_monthly_stats_point_type
feature name = 7_wallet_user_master_wallet_registered_flag
feature name = 7_wallet_user_master_payment_type
feature name = 8_app_user_monthly_stats_toppage_flag
feature name = 8_app_user_monthly_stats_weather_flag
feature name = 8_app_user_monthly_stats_transit_flag
feature name = 8_app_user_monthly_stats_shopping_flag
feature name = 8_app_user_monthly_stats_gyao_flag
feature name = 8_app

features   overlap  train_nans  \
0                                    y_id_hex  1.250222           0   
1                    1_y_id_master_chkyj_flag  1.000000           0   
2  2_user_profile_master_commerce_generation1  1.000000           0   
3  2_user_profile_master_commerce_generation3  1.000000           0   
4  2_user_profile_master_commerce_generation5  1.000000           0   

   test_nans  train_nunique  test_nunique  
0          0           3381           846  
1          0              2             1  
2          0              6             6  
3          0             12            12  
4          0             14            14

In [24]:
chkc.style.background_gradient()

In [25]:
# remove features with too many nans
cat_features = chkc.loc[chkc["train_nans"] < 3000, "features"].values.tolist()
print(cat_features)

['y_id_hex', '1_y_id_master_chkyj_flag', '2_user_profile_master_commerce_generation1', '2_user_profile_master_commerce_generation3', '2_user_profile_master_commerce_generation5', '2_user_profile_master_commerce_chkyj_flag', '2_user_profile_master_commerce_premium_user_flag', '2_user_profile_master_commerce_wallet_registered_flag', '2_user_profile_master_commerce_valid_card_count', '2_user_profile_master_commerce_auction_store_flag', '6_point_user_monthly_stats_point_type', '7_wallet_user_master_wallet_registered_flag', '7_wallet_user_master_payment_type', '8_app_user_monthly_stats_toppage_flag', '8_app_user_monthly_stats_weather_flag', '8_app_user_monthly_stats_transit_flag', '8_app_user_monthly_stats_shopping_flag', '8_app_user_monthly_stats_gyao_flag', '8_app_user_monthly_stats_auctions_flag', '8_app_user_monthly_stats_mail_flag', '8_app_user_monthly_stats_yjtrend_flag', '8_app_user_monthly_stats_apppkgcal_flag', '8_app_user_monthly_stats_ymail_flag', '8_app_user_monthly_stats_emg_fl

# Fit LGB and Get Feature importance

In [26]:
for f in features:
    if X_train[f].dtype == "bool":
        X_train[f] = X_train[f].astype(int)
        X_test[f] = X_test[f].astype(int)
X_train = X_train.replace([np.inf, -np.inf], np.nan)
X_test = X_test.replace([np.inf, -np.inf], np.nan)

In [27]:
# label encoding object features
train, test = label_encoding(X_train, X_test, cat_features)
train.head()

y_id_hex  1_y_id_master_gender  1_y_id_master_birthday  \
0      18.0                     1                     NaN   
1     220.0                     1                     NaN   
2      93.0                     1                     NaN   
3     184.0                     1                     NaN   
4      17.0                     2                     NaN   

   1_y_id_master_registration_date  1_y_id_master_first_update  \
0                         20030216                  20080701.0   
1                         20150111                  20150116.0   
2                         20170212                  20170217.0   
3                         20080810                  20080814.0   
4                         20170611                  20170617.0   

   1_y_id_master_last_update  1_y_id_master_age  \
0                   20191201               38.0   
1                   20191119               28.0   
2                   20191130               53.0   
3                   20191201               39.0   
4                   20191201               46.0   

   1_y_id_master_registration_month  1_y_id_master_registration_week  \
0                               202                              876   
1                                59                              255   
2                                34                              146   
3                               136                              590   
4                                30                              129   

   1_y_id_master_chkyj_flag  ...  \
0                       0.0  ...   
1                       0.0  ...   
2                       0.0  ...   
3                       0.0  ...   
4                       0.0  ...   

   99_yup_user_daily_score_2_interest_know_well_world_history  \
0                                                NaN            
1                                                NaN            
2                                                NaN            
3                                                NaN            
4                                                NaN            

   99_yup_user_daily_score_2_interest_know_well_art  \
0                                               NaN   
1                                               NaN   
2                                               NaN   
3                                               NaN   
4                                          0.035332   

   99_yup_user_daily_score_2_interest_know_well_iphone  \
0                                                NaN     
1                                                NaN     
2                                                NaN     
3                                                NaN     
4                                                NaN     

   99_yup_user_daily_score_2_interest_know_well_android  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                NaN      
4                                                NaN      

   99_yup_user_daily_score_2_interest_know_well_pc  \
0                                         0.022498   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

   99_yup_user_daily_score_2_interest_know_well_home_appliance  \
0                                                NaN             
1                                                NaN             
2                                                NaN             
3                                           0.026999             
4                                           0.006862             

   99_yup_user_daily_score_2_interest_starting_own_business  \
0                                                NaN          
1       

In [28]:
train[target].isna().sum()

0

In [29]:
test[target].isna().sum()

0

In [30]:
features = dense_features + cat_features
target in features

False

In [31]:
# fit LGB
lgbcls = LgbClassifier(train, test, target, features, categoricals=cat_features, cv_method="StratifiedKFold")

Training until validation scores don't improve for 100 rounds
[100]	training's auc: 1	valid_1's auc: 1
Early stopping, best iteration is:
[1]	training's auc: 1	valid_1's auc: 1


ValueError: Input contains NaN, infinity or a value too large for dtype('float64').

In [ ]:
# plot feature importance
lgbcls.plot_feature_importance(rank_range=[1,100])